# Shopping basket analysis of a bakery
#### Databricks Free Edition Hackathon from November 5-14, 2025
author: "Vladimir Poliakov"

##1 Introduction
Every single company, that sells something, automatically has the data, whether in electronic format or on paper, for shopping or market basket analysis. And bakeries are no exception in this regard. The large retailers use usual the Apriori algorithm. This notebook should present this algorithm on the sales transactions dataset one small bakery. The scope is to demonstrate here, even the small bakery can get more profit from shopping basket analysis or in other words from Data Science.  

##2 Theory
As menshioned above for the market will be used basket the Apriori algorithm. The algorithm tries to uncover associations between items in the basket (the searching for the strong rules also known as Association Rules).

Please check in the following links for more information:
* Association rule learning on Wikipedia: https://en.wikipedia.org/wiki/Association_rule_learning
* KDnuggets: https://www.kdnuggets.com/2016/04/association-rules-apriori-algorithm-tutorial.html

The key metrics the Apriori algorithm are: Support, Confidence and Lift.

**Support**
Support answers the question, how popular an itemset is, or how often appear an itemset in all transactions.<br>
support(A,B) = (transactions with A and B) / (total Transaktionen)

**Confidence**
The confidence (A -> A) indicates how often A is purchased when B is purchased.<br>
confidence(A→B) = (transactions with A and B) / (transactions with A)

**Lift**
The lift provides the answer to the question of how much more likely A makes the purchase of B.<br>
lift(A,B) = support(A,B) / (support(A) x support(B))

##3 Loading data into Bronze table
The dataset was downloaded from Kaggle service https://www.kaggle.com/sulmansarwar/transactions-from-a-bakery

Dataset description from Kaggle:

_The dataset consists of 21293 observations from a bakery. The data file contains four variables, Date, Time, Transaction ID and Item. Transaction ID ranges from 1 through 9684. However, there are some skipped numbers in Transaction IDs. Also, there are duplicated entries, as shown in observation # 2 and #3. Besides, the Item contains "Adjustment", "NONE", and "Afternoon with the baker". While the entries of "Adjustment" and "NONE" are straight forward, "Afternoon with the baker" may be a real purchase._

The statemet about duplicated entries is not really correct. It could be really many items in the shopping basket, what means the item was bought double, three tiems etc.

In [0]:
from pyspark.sql import functions as F

# It is not really neccessary to transform the CSV into bronze table in this case, but we do following best practices
# Read the CSV an transform into bronze table: Raw Ingestion
bronze_df = spark.read.csv("/Volumes/workspace/default/input/BreadBasket_DMS.csv", header=True, inferSchema=True, sep=",")
bronze_df = bronze_df.withColumn("Ingest_ts", F.current_timestamp())
bronze_df.write.mode("overwrite").saveAsTable("workspace.default.bronze_basket_transactions")

bronze_df.printSchema()
display(bronze_df)

root
 |-- Date: date (nullable = true)
 |-- Time: timestamp (nullable = true)
 |-- Transaction: integer (nullable = true)
 |-- Item: string (nullable = true)
 |-- Ingest_ts: timestamp (nullable = false)



Date Time Transaction Item Ingest_ts 2016-10-30 2025-11-11T09:58:11.000Z 1 Bread 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:05:34.000Z 2 Scandinavian 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:05:34.000Z 2 Scandinavian 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:07:57.000Z 3 Hot chocolate 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:07:57.000Z 3 Jam 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:07:57.000Z 3 Cookies 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:08:41.000Z 4 Muffin 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:13:03.000Z 5 Coffee 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:13:03.000Z 5 Pastry 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:13:03.000Z 5 Bread 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:16:55.000Z 6 Medialuna 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:16:55.000Z 6 Pastry 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:16:55.000Z 6 Muffin 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:19:12.000Z 7 Medialuna 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:19:12.000Z 7 Pastry 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:19:12.000Z 7 Coffee 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:19:12.000Z 7 Tea 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:20:51.000Z 8 Pastry 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:20:51.000Z 8 Bread 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:21:59.000Z 9 Bread 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:21:59.000Z 9 Muffin 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:25:58.000Z 10 Scandinavian 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:25:58.000Z 10 Medialuna 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:27:21.000Z 11 Bread 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:27:21.000Z 11 Medialuna 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:27:21.000Z 11 Bread 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:27:21.000Z 11 NONE 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:30:14.000Z 12 Jam 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:30:14.000Z 12 Coffee 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:30:14.000Z 12 Tartine 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:30:14.000Z 12 Pastry 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:30:14.000Z 12 Tea 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:31:24.000Z 13 Basket 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:31:24.000Z 13 Bread 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:31:24.000Z 13 Coffee 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:32:46.000Z 14 Bread 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:32:46.000Z 14 Medialuna 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:32:46.000Z 14 Pastry 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:34:36.000Z 15 NONE 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:34:36.000Z 15 NONE 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:34:36.000Z 15 Mineral water 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:34:36.000Z 15 Scandinavian 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:37:08.000Z 16 Bread 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:37:08.000Z 16 Medialuna 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:37:08.000Z 16 Coffee 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:38:04.000Z 17 Hot chocolate 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:41:56.000Z 18 Farm House 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:43:08.000Z 19 Farm House 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:43:08.000Z 19 Bread 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:45:22.000Z 20 Bread 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:45:22.000Z 20 Medialuna 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:49:29.000Z 21 Coffee 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:49:29.000Z 21 Coffee 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:49:29.000Z 21 Medialuna 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:49:29.000Z 21 Bread 2025-11-11T08:00:22.497Z 2016-10-30 2025-11-11T10:52:15

In [0]:
# Let's have a look at the statistics
bronze_df.describe().show()

+-------+------------------+----------------+
|summary|       Transaction|            Item|
+-------+------------------+----------------+
|  count|             21293|           21293|
|   mean| 4951.990889024562|            NULL|
| stddev|2787.7583996983767|            NULL|
|    min|                 1|      Adjustment|
|    max|              9684|Victorian Sponge|
+-------+------------------+----------------+



##4 Cleaning data and loading it into Silver table

In [0]:
# As menshoned above delete all transaction with "Adjustment", "NONE", and "Afternoon with the baker",
# because we want to know the real existing items
silver_df = bronze_df.filter(bronze_df.Item.isNotNull() & bronze_df.Transaction.isNotNull())

# Filer only items, which do NOT have "Adjustment", "NONE", and "Afternoon with the baker" values
silver_df = silver_df.filter(~(bronze_df.Item.isin(["Adjustment", "NONE", "Afternoon with the baker"])))

silver_df = silver_df \
    .withColumn("Year", F.year("Date")) \
    .withColumn("Month", F.month("Date")) \
    .withColumn("Day", F.dayofmonth("Date")) \
    .withColumn("Hour", F.hour("Time")) \
    .withColumn("Minute", F.minute("Time"))

silver_df.write.mode("overwrite").saveAsTable("workspace.default.silver_basket_transactions")
silver_df.printSchema()
display(silver_df)

root
 |-- Date: date (nullable = true)
 |-- Time: timestamp (nullable = true)
 |-- Transaction: integer (nullable = true)
 |-- Item: string (nullable = true)
 |-- Ingest_ts: timestamp (nullable = false)
 |-- Year: integer (nullable = true)
 |-- Month: integer (nullable = true)
 |-- Day: integer (nullable = true)
 |-- Hour: integer (nullable = true)
 |-- Minute: integer (nullable = true)



Date Time Transaction Item Ingest_ts Year Month Day Hour Minute 2016-10-30 2025-11-11T09:58:11.000Z 1 Bread 2025-11-11T08:00:42.623Z 2016 10 30 9 58 2016-10-30 2025-11-11T10:05:34.000Z 2 Scandinavian 2025-11-11T08:00:42.623Z 2016 10 30 10 5 2016-10-30 2025-11-11T10:05:34.000Z 2 Scandinavian 2025-11-11T08:00:42.623Z 2016 10 30 10 5 2016-10-30 2025-11-11T10:07:57.000Z 3 Hot chocolate 2025-11-11T08:00:42.623Z 2016 10 30 10 7 2016-10-30 2025-11-11T10:07:57.000Z 3 Jam 2025-11-11T08:00:42.623Z 2016 10 30 10 7 2016-10-30 2025-11-11T10:07:57.000Z 3 Cookies 2025-11-11T08:00:42.623Z 2016 10 30 10 7 2016-10-30 2025-11-11T10:08:41.000Z 4 Muffin 2025-11-11T08:00:42.623Z 2016 10 30 10 8 2016-10-30 2025-11-11T10:13:03.000Z 5 Coffee 2025-11-11T08:00:42.623Z 2016 10 30 10 13 2016-10-30 2025-11-11T10:13:03.000Z 5 Pastry 2025-11-11T08:00:42.623Z 2016 10 30 10 13 2016-10-30 2025-11-11T10:13:03.000Z 5 Bread 2025-11-11T08:00:42.623Z 2016 10 30 10 13 2016-10-30 2025-11-11T10:16:55.000Z 6 Medialuna 2025-11-11T08:00:42.623Z 2016 10 30 10 16 2016-10-30 2025-11-11T10:16:55.000Z 6 Pastry 2025-11-11T08:00:42.623Z 2016 10 30 10 16 2016-10-30 2025-11-11T10:16:55.000Z 6 Muffin 2025-11-11T08:00:42.623Z 2016 10 30 10 16 2016-10-30 2025-11-11T10:19:12.000Z 7 Medialuna 2025-11-11T08:00:42.623Z 2016 10 30 10 19 2016-10-30 2025-11-11T10:19:12.000Z 7 Pastry 2025-11-11T08:00:42.623Z 2016 10 30 10 19 2016-10-30 2025-11-11T10:19:12.000Z 7 Coffee 2025-11-11T08:00:42.623Z 2016 10 30 10 19 2016-10-30 2025-11-11T10:19:12.000Z 7 Tea 2025-11-11T08:00:42.623Z 2016 10 30 10 19 2016-10-30 2025-11-11T10:20:51.000Z 8 Pastry 2025-11-11T08:00:42.623Z 2016 10 30 10 20 2016-10-30 2025-11-11T10:20:51.000Z 8 Bread 2025-11-11T08:00:42.623Z 2016 10 30 10 20 2016-10-30 2025-11-11T10:21:59.000Z 9 Bread 2025-11-11T08:00:42.623Z 2016 10 30 10 21 2016-10-30 2025-11-11T10:21:59.000Z 9 Muffin 2025-11-11T08:00:42.623Z 2016 10 30 10 21 2016-10-30 2025-11-11T10:25:58.000Z 10 Scandinavian 2025-11-11T08:00:42.623Z 2016 10 30 10 25 2016-10-30 2025-11-11T10:25:58.000Z 10 Medialuna 2025-11-11T08:00:42.623Z 2016 10 30 10 25 2016-10-30 2025-11-11T10:27:21.000Z 11 Bread 2025-11-11T08:00:42.623Z 2016 10 30 10 27 2016-10-30 2025-11-11T10:27:21.000Z 11 Medialuna 2025-11-11T08:00:42.623Z 2016 10 30 10 27 2016-10-30 2025-11-11T10:27:21.000Z 11 Bread 2025-11-11T08:00:42.623Z 2016 10 30 10 27 2016-10-30 2025-11-11T10:30:14.000Z 12 Jam 2025-11-11T08:00:42.623Z 2016 10 30 10 30 2016-10-30 2025-11-11T10:30:14.000Z 12 Coffee 2025-11-11T08:00:42.623Z 2016 10 30 10 30 2016-10-30 2025-11-11T10:30:14.000Z 12 Tartine 2025-11-11T08:00:42.623Z 2016 10 30 10 30 2016-10-30 2025-11-11T10:30:14.000Z 12 Pastry 2025-11-11T08:00:42.623Z 2016 10 30 10 30 2016-10-30 2025-11-11T10:30:14.000Z 12 Tea 2025-11-11T08:00:42.623Z 2016 10 30 10 30 2016-10-30 2025-11-11T10:31:24.000Z 13 Basket 2025-11-11T08:00:42.623Z 2016 10 30 10 31 2016-10-30 2025-11-11T10:31:24.000Z 13 Bread 2025-11-11T08:00:42.623Z 2016 10 30 10 31 2016-10-30 2025-11-11T10:31:24.000Z 13 Coffee 2025-11-11T08:00:42.623Z 2016 10 30 10 31 2016-10-30 2025-11-11T10:32:46.000Z 14 Bread 2025-11-11T08:00:42.623Z 2016 10 30 10 32 2016-10-30 2025-11-11T10:32:46.000Z 14 Medialuna 2025-11-11T08:00:42.623Z 2016 10 30 10 32 2016-10-30 2025-11-11T10:32:46.000Z 14 Pastry 2025-11-11T08:00:42.623Z 2016 10 30 10 32 2016-10-30 2025-11-11T10:34:36.000Z 15 Mineral water 2025-11-11T08:00:42.623Z 2016 10 30 10 34 2016-10-30 2025-11-11T10:34:36.000Z 15 Scandinavian 2025-11-11T08:00:42.623Z 2016 10 30 10 34 2016-10-30 2025-11-11T10:37:08.000Z 16 Bread 2025-11-11T08:00:42.623Z 2016 10 30 10 37 2016-10-30 2025-11-11T10:37:08.000Z 16 Medialuna 2025-11-11T08:00:42.623Z 2016 10 30 10 37 2016-10-30 2025-11-11T10:37:08.000Z 16 Coffee 2025-11-11T08:00:42.623Z 2016 10 30 10 37 2016-10-30 2025-11-11T10:38:04.000Z 17 Hot chocolate 2025-11-11T08:00:42.623Z 2016 10 30 10 38 2016-10-30 2025-11-11T10:41:56.000Z 18 Farm House 2025-11-11T08:00:42.623Z 2016 10 30 10 41 2016-10-30 2025-11-11T10:43:08.000Z 19 Farm 

In [0]:
# Finally we have 831 rows less
silver_df.describe().show()

+-------+-----------------+----------------+------------------+-----------------+------------------+------------------+------------------+
|summary|      Transaction|            Item|              Year|            Month|               Day|              Hour|            Minute|
+-------+-----------------+----------------+------------------+-----------------+------------------+------------------+------------------+
|  count|            20462|           20462|             20462|            20462|             20462|             20462|             20462|
|   mean|4973.121688984459|            NULL|2016.6020428110644|5.868439057765614|15.106245723780667|12.266347375623106|29.274411103508942|
| stddev|2797.425834581686|            NULL|0.4894884821629984|4.543754870191641| 8.942515050378683| 2.332470512000763|17.533145221337616|
|    min|                1|       Alfajores|              2016|                1|                 1|                 1|                 0|
|    max|             9684|

In [0]:
# Let's have a look at the unique items. We should have 92 unique items
unique_items = silver_df.select("Item").distinct()
assert unique_items.count() == 92, "There should be 92 unique items"
display(unique_items)

Item Duck egg Tiffin Half slice Monster Mineral water Fudge Argentina Night Vegan mincepie Siblings Keeping It Local Focaccia Victorian Sponge Kids biscuit Olum & polenta Caramel bites Basket Toast Muesli Pastry Baguette Truffles Muffin Bacon Chicken Stew The Nomad Postcard Honey Gift voucher Tartine Smoothies Bread Salad Valentine's card Jammie Dodgers Cookies Ella's Kitchen Pouches Pintxos Bread Pudding Vegan Feast Medialuna Spread Panatone Mortimer Empanadas Hot chocolate Dulce de Leche Soup Chicken sand Tea Christmas common Bowl Nic Pitt Scandinavian Chocolates Coke Chimichurri Oil Juice Coffee granules Nomad bag Brownie Drinking chocolate spoons Bare Popcorn Coffee Cherry me Dried fruit Tacos/Fajita Raw bars Extra Salami or Feta Eggs Cake My-5 Fruit Shoot Spanish Brunch Art Tray Pick and Mix Bowls The BART Raspberry shortbread sandwich Scone Crisps Gingerbread syrup Mighty Protein Hearty & Seasonal Fairy Doors Lemon and coconut Jam Frittata Granola Bakewell Alfajores Crepes Polenta Tshirt Sandwich Brioche and salami Hack the stack Farm House

## 5 Visualizing and Understanding the Data
The dataset has the transactions from 2016-10-30 until 2017-04-09. Let's try to answer for some questions
* Which items do customers buy most? 
* Which months were more successful?
* Which hours are the rush hours?

In [0]:
%sql
-- Which items do customers buy most? Let see the 10 most popular items
-- Logically the most popular items should be Coffee and Bread
SELECT Item, count(Item) AS Count_Item FROM default.silver_basket_transactions GROUP BY Item ORDER BY Count_Item DESC LIMIT 10;

Item Count_Item Coffee 5471 Bread 3325 Tea 1435 Cake 1025 Pastry 856 Sandwich 771 Medialuna 616 Hot chocolate 590 Cookies 540 Brownie 379

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
-- Which months were more successful?
-- The most successful month was November, but there are not data for some months
SELECT Month, count(Item) AS Count_Item FROM default.silver_basket_transactions GROUP BY ALL ORDER BY Count_Item DESC;

Month Count_Item 11 4435 3 3930 2 3893 1 3341 12 3339 4 1155 10 369

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
-- Which hours are the rush hours?
SELECT Hour, count(Item) AS Count_Item FROM default.silver_basket_transactions GROUP BY ALL ORDER BY Hour, Count_Item;

Hour Count_Item 1 1 7 24 8 642 9 1964 10 2662 11 3101 12 2851 13 2615 14 2631 15 2111 16 1342 17 367 18 68 19 47 20 22 21 3 22 8 23 3

Databricks visualization. Run in Databricks to view.

##6 Shopping basket analysis
For the small to medium datasets we can use `mlxtend` package, because it’s simpler and Pandas-based. However, approach in a Databricks environment is to leverage its distributed computing power from the start. For that reason, using the `FPGrowth` class from Spark MLlib is more preferable, since the order of items in the basket is not important. `FPGrowth` is designed for distributed processing and works perfectly in Databricks, making it future-proof if the dataset grows significantly.

**Warning**: Since the Databricks Free Editon is limited to Serverless Compute and the solution with `FPGrowth` does not work _[CONNECT_ML.UNSUPPORTED_EXCEPTION] Generic Spark Connect ML error. FPGrowth algorithm is not supported if Spark Connect model cache offloading is enabled. SQLSTATE: XX000_, let us try to implement Market Basket Analysis using pure PySpark SQL.

For the market basket analysis using FP-growth on Databricks s. the blog article: https://www.databricks.com/blog/2018/09/18/simplify-market-basket-analysis-using-fp-growth-on-databricks.html

In [0]:
%sql
-----------------------------
-- Pure PySpark SQL Solution
-- ¯\_(ツ)_/¯
-----------------------------
-- Generate Item Pairs per Transaction (excluding self-pairs)
CREATE OR REPLACE TEMP VIEW item_pairs AS
SELECT
    a.Item AS item_A,
    b.Item AS item_B,
    a.Transaction
FROM default.silver_basket_transactions a
JOIN default.silver_basket_transactions b
ON a.Transaction = b.Transaction
WHERE a.item != b.item;  -- avoid duplicates and self-pairs

-- Total number of transactions
CREATE OR REPLACE TEMP VIEW total_tx AS
SELECT COUNT(DISTINCT Transaction) AS total_tx
FROM default.silver_basket_transactions;

-- Item frequency
CREATE OR REPLACE TEMP VIEW item_freq AS
SELECT item, COUNT(DISTINCT Transaction) AS item_count
FROM default.silver_basket_transactions
GROUP BY item;

-- Pair frequency
CREATE OR REPLACE TEMP VIEW pair_freq AS
SELECT item_A, item_B, COUNT(DISTINCT Transaction) AS pair_count
FROM item_pairs
GROUP BY item_A, item_B;

-- Calculate Support, Confidence, Lift and safe it into gold table for late analysis by Genie
CREATE OR REPLACE TABLE gold_basket_transactions AS
SELECT
    pf.item_A,
    pf.item_B,
    pf.pair_count,
    iA.item_count AS item_A_count,
    iB.item_count AS item_B_count,
    ROUND(pf.pair_count / t.total_tx, 4) AS support,
    ROUND(pf.pair_count / iA.item_count, 4) AS confidence_A_to_B,
    ROUND(pf.pair_count / iB.item_count, 4) AS confidence_B_to_A,
    ROUND((pf.pair_count / t.total_tx) / ((iA.item_count / t.total_tx) * (iB.item_count / t.total_tx)), 4) AS lift
FROM pair_freq pf
JOIN item_freq iA ON pf.item_A = iA.item
JOIN item_freq iB ON pf.item_B = iB.item
CROSS JOIN total_tx t
ORDER BY lift DESC;


num_affected_rows num_inserted_rows

##7 Conclusion

* Using SQL instead of the FPGrowth class from Spark MLlib for Market Basket Analysis may not be the best solution, especially when dealing with many products in the market basket. However, it is sufficient for a hackathon to demonstrate an alternative Databricks distributed solution.
* The Genie in the Databricks platform helps perform analysis in descriptive language without requiring knowledge of SQL.

## Summary
* Dataset from Kaggle:<br>
https://www.kaggle.com/datasets/sulmansarwar/transactions-from-a-bakery
* Affinity analysis on Wikipedia:<br>
https://en.wikipedia.org/wiki/Affinity_analysis
* Association Rules and the Apriori Algorithm: A Tutorial on KDnuggets:<br>
https://www.kdnuggets.com/2016/04/association-rules-apriori-algorithm-tutorial.html
* Simplify Market Basket Analysis using FP-growth on Databricks:<br>
https://www.databricks.com/blog/2018/09/18/simplify-market-basket-analysis-using-fp-growth-on-databricks.html
* Warenkorbanalyse einer Bäckerei (Repo on GitHub in German):<br>
https://github.com/VladiPol/ds4all/blob/master/baeckerei_warenkorbanalyse.ipynb
